## Web Scraping

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline
import re
import time
from datetime import datetime
import matplotlib.dates as mdates
import matplotlib.ticker as ticker
from urllib.request import urlopen
from bs4 import BeautifulSoup
import requests
import warnings
warnings.filterwarnings('ignore')
print('Setup Complete!')


Setup Complete!


In [2]:
no_pages = 2

def get_data(pageNo):
    headers = {"User-Agent":"Mozilla/5.0 (Windows NT 10.0; Win64; x64; rv:66.0) Gecko/20100101 Firefox/66.0", "Accept-Encoding":"gzip, deflate", "Accept":"text/html,application/xhtml+xml,application/xml;q=0.9,*/*;q=0.8", "DNT":"1","Connection":"close", "Upgrade-Insecure-Requests":"1"}

    r = requests.get('https://www.amazon.com/gp/bestsellers/books/ref=zg_bs_pg_'+str(pageNo)+'?ie=UTF8&pg='+str(pageNo), headers=headers)#, proxies=proxies)
    content = r.content
    soup = BeautifulSoup(content)
    #print(soup)

    alls = []
    for d in soup.findAll('div', attrs={'class':'a-section a-spacing-none aok-relative'}):
        #print(d)
        name = d.find('span', attrs={'class':'zg-text-center-align'})
        n = name.find_all('img', alt=True)
        #print(n[0]['alt'])
        author = d.find('a', attrs={'class':'a-size-small a-link-child'})
        rating = d.find('span', attrs={'class':'a-icon-alt'})
        users_rated = d.find('a', attrs={'class':'a-size-small a-link-normal'})
        price = d.find('span', attrs={'class':'p13n-sc-price'})

        all1=[]

        if name is not None:
            #print(n[0]['alt'])
            all1.append(n[0]['alt'])
        else:
            all1.append("unknown-product")

        if author is not None:
            #print(author.text)
            all1.append(author.text)
        elif author is None:
            author = d.find('span', attrs={'class':'a-size-small a-color-base'})
            if author is not None:
                all1.append(author.text)
            else:
                all1.append('0')

        if rating is not None:
            #print(rating.text)
            all1.append(rating.text)
        else:
            all1.append('-1')

        if users_rated is not None:
            #print(price.text)
            all1.append(users_rated.text)
        else:
            all1.append('0')

        if price is not None:
            #print(price.text)
            all1.append(price.text)
        else:
            all1.append('0')
        alls.append(all1)
    return alls

In [3]:
results = []
for i in range(1, no_pages+1):
    results.append(get_data(i))
flatten = lambda l: [item for sublist in l for item in sublist]
df = pd.DataFrame(flatten(results),columns=['Book Name','Author','Rating','Customers_Rated', 'Price'])
df.to_csv('amazon_products.csv', index=False, encoding='utf-8')

In [5]:
data = pd.read_csv("amazon_products.csv")

In [6]:
data.shape

(0, 5)

In [7]:
data.head()

Empty DataFrame
Columns: [Book Name, Author, Rating, Customers_Rated, Price]
Index: []

In [8]:
data.tail()

Empty DataFrame
Columns: [Book Name, Author, Rating, Customers_Rated, Price]
Index: []

In [9]:
data.info()

<class 'pandas.core.frame.DataFrame'>
Index: 0 entries
Data columns (total 5 columns):
 #   Column           Non-Null Count  Dtype 
---  ------           --------------  ----- 
 0   Book Name        0 non-null      object
 1   Author           0 non-null      object
 2   Rating           0 non-null      object
 3   Customers_Rated  0 non-null      object
 4   Price            0 non-null      object
dtypes: object(5)
memory usage: 0.0+ bytes


In [10]:
data['Rating'] = data['Rating'].apply(lambda x: x.split()[0])
data['Rating'] = pd.to_numeric(data['Rating'])
data["Price"] = data["Price"].str.replace('$', '')
data["Price"] = data["Price"].str.replace(',', '')
data['Price'] = data['Price'].apply(lambda x: x.split('.')[0])
data['Price'] = data['Price'].astype(int)
data["Customers_Rated"] = data["Customers_Rated"].str.replace(',', '')
data['Customers_Rated'] = pd.to_numeric(data['Customers_Rated'], errors='ignore')
data.head()

Empty DataFrame
Columns: [Book Name, Author, Rating, Customers_Rated, Price]
Index: []

In [11]:
data.dtypes

Book Name          object
Author             object
Rating              int64
Customers_Rated     int64
Price               int64
dtype: object

In [12]:
## Replace the zero values in the DataFrame to NaN.
data.replace(str(0), np.nan, inplace=True)
data.replace(0, np.nan, inplace=True)

In [13]:
## Counting the Number of NaNs in the DataFrame
count_nan = len(data) - data.count()
count_nan

Book Name          0
Author             0
Rating             0
Customers_Rated    0
Price              0
dtype: int64

In [14]:
## Let's drop these NaNs.
data = data.dropna()

In [19]:
Data = data.sort_values(["Price"], axis=0, ascending=False)[:15]
Data

Empty DataFrame
Columns: [Book Name, Author, Rating, Customers_Rated, Price]
Index: []

In [20]:
from bokeh.models import ColumnDataSource
from bokeh.transform import dodge
import math
from bokeh.io import curdoc
curdoc().clear()
from bokeh.io import push_notebook, show, output_notebook
from bokeh.layouts import row
from bokeh.plotting import figure
from bokeh.transform import factor_cmap
from bokeh.models import Legend
output_notebook()

In [25]:
p = figure(x_range=Data.iloc[:,1],min_width=800,min_height=550, title="Authors Highest Priced Book", toolbar_location=None, tools="")

p.vbar(x=Data.iloc[:,1], top=Data.iloc[:,4], width=0.9)

p.xgrid.grid_line_color = None
p.y_range.start = 0
p.xaxis.major_label_orientation = math.pi/2

In [29]:
show(p)

In [28]:
Data = data[data['Customers_Rated'] > 1000]
Data = Data.sort_values(['Rating'],axis=0, ascending=False)[:15]
Data

Empty DataFrame
Columns: [Book Name, Author, Rating, Customers_Rated, Price]
Index: []

In [30]:
p = figure(x_range=Data.iloc[:,0], min_width=800, min_height=600, title="Top Rated Books with more than 1000 Customers Rating", toolbar_location=None, tools="")

p.vbar(x=Data.iloc[:,0], top=Data.iloc[:,2], width=0.9)

p.xgrid.grid_line_color = None
p.y_range.start = 0
p.xaxis.major_label_orientation = math.pi/2
show(p)

In [32]:
p = figure(x_range=Data.iloc[:,1], min_width=800, min_height=600, title="Top Rated Books with more than 1000 Customers Rating", toolbar_location=None, tools="")

p.vbar(x=Data.iloc[:,1], top=Data.iloc[:,2], width=0.9)

p.xgrid.grid_line_color = None
p.y_range.start = 0
p.xaxis.major_label_orientation = math.pi/2
show(p)

In [33]:
Data = data.sort_values(["Customers_Rated"], axis=0, ascending=False)[:20]

In [34]:
Data

Empty DataFrame
Columns: [Book Name, Author, Rating, Customers_Rated, Price]
Index: []

In [35]:
from bokeh.transform import factor_cmap
from bokeh.models import Legend
from bokeh.palettes import Dark2_5 as palette
import itertools
from bokeh.palettes import d3
#colors has a list of colors which can be used in plots
colors = itertools.cycle(palette)

palette = d3['Category20'][20]

In [36]:
index_cmap = factor_cmap('Author', palette=palette,
                         factors=data["Author"])

In [41]:
p = figure(min_width=700, min_height=700, title = "Top Authors: Rating vs. Customers Rated")
p.scatter('Rating','Customers_Rated',source=data,fill_alpha=0.6, fill_color=index_cmap,size=20)
plt.legend='Author'

p.xaxis.axis_label = 'RATING'
p.yaxis.axis_label = 'CUSTOMERS RATED'
p.legend.location = 'top_left'
show(p)